In [1]:
import kmapper as km

In [7]:
mapper = km.KeplerMapper(verbose=1)

KeplerMapper(verbose=1)


In [2]:
from numpy import pi, sin,cos, dot
import numpy as np
import random
import matplotlib.pyplot as plt
import sklearn
from sklearn.manifold import Isomap
from sklearn.decomposition import PCA
from sklearn.manifold import LocallyLinearEmbedding as LLE
import plotly.graph_objects as go

In [3]:
def graph_continuous(image_function, x, y, x_random = True, n_samples= 100000, y_random = True):
    
    if x_random == True:
        X = list(2 * x * np.random.random(n_samples) - x) 
        if y_random == True:
            Y = list(2 * y * np.random.random(n_samples) - y) 
        else:
            Y = np.linspace(-y,y,n_samples)      

    if x_random == False:
        X = np.linspace(-x,x,n_samples)
        if y_random == True:
            Y = list(2 * y * np.random.random(n_samples) - y) 
        else:
            Y = np.linspace(-y,y,n_samples)   

    x_points = []
    y_points = []
    colors = []
    for i in range(n_samples):
        color = image_function(X[i],Y[i]) 
        colors.append(color)
        x_points.append(X[i])
        y_points.append(Y[i])

        
    fig = plt.figure(figsize = (7, 7))
    ax = plt.axes()
    ax.scatter(x_points, y_points, c = colors, s = .1)
    plt.show()
    
def view_window_continuous(image_function, num_pixels, window_size):
    
    pixels = get_pixels(num_pixels, window_size)
            
    x_points = []
    y_points = []
    colors = []
    for i in range(len(pixels)):
        color = image_function(pixels[i][0],pixels[i][1]) 
        colors.append(color)
        x_points.append(pixels[i][0])
        y_points.append(pixels[i][1])
    
    fig = plt.figure(figsize = (7, 7))
    ax = plt.axes()
    ax.scatter(x_points, y_points, c = colors)
    plt.show()
    
def get_pixels(num_pixels, window_size):
    sample = list(np.linspace(-window_size/2, window_size/2, num_pixels))
    pixels = []
    for i in range(len(sample)):
        for j in range(len(sample)):
            pixels.append((sample[i],sample[j]))     
    return pixels


def get_colors(pixels, image_function):
    colors = []
    for pixel in pixels:
        colors.append(image_function(pixel[0],pixel[1]))
    return colors  

def translation(a,b):
    def t_ab(x,y): 
        return x+a, y+b
    return t_ab

def rotation(theta):
    def r_theta(x,y):
        return x * cos(theta) - y * sin(theta), x * sin(theta) + y * cos(theta)
    return r_theta

def isom(a,b,theta):
    def iso(x,y):
        r = rotation(theta)
        t = translation(a,b)
        return t(r(x,y)[0], r(x,y)[1])
    return iso

def generate_isom(n_isos, x_translate, y_translate):
    a = list(2 * x_translate * np.random.random(n_isos) - x_translate) # sampling from (-x,x)
    b = list(2 * y_translate * np.random.random(n_isos) - y_translate) # sampling from (-y,y)
    theta = list(2 * pi * np.random.random(n_isos)) # sampling from (0, 2pi)

    isos = []
    isos_inv = []
    for i in range(n_isos):
        isos.append(isom(a[i], b[i], theta[i]))
        isos_inv.append(isom(-1 * a[i],-1 * b[i],2 * pi - theta[i])) 
    return isos_inv

def new_colors(pixels, iso_inv, image_function):
    pixels_inv = []
    for pixel in pixels: 
        pixels_inv.append(iso_inv(pixel[0], pixel[1]))
    new_colors = get_colors(pixels_inv, image_function)
    return new_colors

def matrix_of_images(pixels, isos_inv, image_function):
    vectors = []
    for i in isos_inv:
        vectors.append([new_colors(pixels, i, image_function)])
    M = np.concatenate(vectors, axis=0 )
    return M

def data_matrix(image_function, num_pixels, window_size, n_isos, x_translate, y_translate):
    pixels = get_pixels(num_pixels, window_size)
    isos_inv = generate_isom(n_isos, x_translate, y_translate)
    M = matrix_of_images(pixels, isos_inv, image_function)
    return M

In [4]:
def p3_sin(x,y):
    X = 1/(2 * pi) * (x + y / (3**(1/2)))
    Y = 1/(2 * pi) * 2 * y / (3**(1/2))
    C = cos(X + Y) + cos(X - 2 * Y) + cos(-2 * X + Y)
    S = sin(X + Y) +sin(X - 2*Y) +sin(-2 * X + Y)
    return S

In [5]:
M = data_matrix(image_function = p3_sin, num_pixels = 40 , window_size = 50, n_isos = 2000, x_translate= 200 , y_translate=200)

In [14]:
import umap.umap_ as umap
projected_data = mapper.fit_transform(M, projection=umap.UMAP(n_components=3))
projected_data.shape

/Users/oliviamcgough/opt/anaconda3/lib/python3.9/site-packages/umap/distances.py:1063: NumbaDeprecationWarning: The 'nopython' keyword argument was not supplied to the 'numba.jit' decorator. The implicit default value for this argument is currently False, but it will be changed to True in Numba 0.59.0. See https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-object-mode-fall-back-behaviour-when-using-jit for details.
  @numba.jit()
/Users/oliviamcgough/opt/anaconda3/lib/python3.9/site-packages/umap/distances.py:1071: NumbaDeprecationWarning: The 'nopython' keyword argument was not supplied to the 'numba.jit' decorator. The implicit default value for this argument is currently False, but it will be changed to True in Numba 0.59.0. See https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-object-mode-fall-back-behaviour-when-using-jit for details.
  @numba.jit()
/Users/oliviamcgough/opt/anaconda3/lib/python3.9/site-packages/umap/dist

..Composing projection pipeline of length 1:
	Projections: UMAP(n_components=3)
	Distance matrices: False
	Scalers: MinMaxScaler()
..Projecting on data shaped (2000, 1600)

..Projecting data using: 
	UMAP(n_components=3, verbose=1)

UMAP(n_components=3, verbose=1)
Tue Jun 27 10:22:23 2023 Construct fuzzy simplicial set
Tue Jun 27 10:22:25 2023 Finding Nearest Neighbors
Tue Jun 27 10:22:26 2023 Finished Nearest Neighbor Search
Tue Jun 27 10:22:27 2023 Construct embedding


Epochs completed:   0%|            0/500 [00:00]

Tue Jun 27 10:22:28 2023 Finished embedding

..Scaling with: MinMaxScaler()



(2000, 3)

In [16]:
cover = km.Cover(n_cubes=10,verbose =0)
graph = mapper.map(projected_data, M, clusterer = sklearn.cluster.DBSCAN(eps=50, min_samples=10), cover = cover)
graph

Mapping on data shaped (2000, 1600) using lens shaped (2000, 3)

Creating 1000 hypercubes.

Created 3792 edges and 541 nodes in 0:00:00.436053.


{'nodes': defaultdict(list,
             {'cube3_cluster0': [155,
               217,
               244,
               371,
               402,
               448,
               707,
               725,
               1114,
               1239,
               1240,
               1642],
              'cube4_cluster0': [155,
               217,
               244,
               290,
               371,
               402,
               707,
               725,
               1114,
               1239,
               1240],
              'cube9_cluster0': [36,
               279,
               347,
               582,
               695,
               790,
               869,
               875,
               894,
               920,
               952,
               1272,
               1448,
               1669,
               1788,
               1907],
              'cube10_cluster0': [36,
               347,
               448,
               790,
               869,
      

In [17]:
mapper.visualize(graph,path_html = "mapper_visualization_output_umap1.html")

Wrote visualization to: mapper_visualization_output_umap1.html


'<!DOCTYPE html>\n<html>\n\n<head>\n  <meta charset="utf-8">\n  <meta name="generator" content="KeplerMapper">\n  <title>Kepler Mapper | KeplerMapper</title>\n\n  <link rel="icon" type="image/png" href="http://i.imgur.com/axOG6GJ.jpg" />\n\n  <link href=\'https://fonts.googleapis.com/css?family=Roboto+Mono:700,300\' rel=\'stylesheet\' type=\'text/css\'>\n  <style>* {\n  margin: 0;\n  padding: 0;\n}\n\nhtml, body {\n  height: 100%;\n}\n\nbody {\n  font-family: "Roboto Mono", "Helvetica", sans-serif;\n  font-size: 14px;\n}\n\n#logo {\n  width:  85px;\n  height: 85px;\n}\n\n#display {\n  color: #95A5A6;\n  background: #212121;\n}\n\n#header {\n  background: #111111;\n}\n\n#print {\n  color: #000;\n  background: #FFF;\n}\n\nh1 {\n  font-size: 21px;\n  font-weight: 300;\n  font-weight: 300;\n}\n\nh2 {\n  font-size: 18px;\n  padding-bottom: 20px;\n  font-weight: 300;\n}\n\nh3 {\n  font-size: 14px;\n  font-weight: 700;\n  text-transform: uppercase;\n}\n\nh4 {\n  font-size: 13px;\n  font-weigh

In [19]:
cover = km.Cover(n_cubes=12,verbose =0)
graph = mapper.map(projected_data, M, clusterer = sklearn.cluster.DBSCAN(eps=100, min_samples=10), cover = cover)
graph

Mapping on data shaped (2000, 1600) using lens shaped (2000, 3)

Creating 1728 hypercubes.

Created 4547 edges and 671 nodes in 0:00:00.477753.


{'nodes': defaultdict(list,
             {'cube14_cluster0': [57,
               105,
               531,
               635,
               1053,
               1126,
               1152,
               1172,
               1198,
               1595,
               1649,
               1777],
              'cube15_cluster0': [57,
               105,
               531,
               601,
               635,
               984,
               1053,
               1126,
               1152,
               1172,
               1198,
               1595,
               1649,
               1777],
              'cube17_cluster0': [8,
               20,
               629,
               1189,
               1195,
               1336,
               1412,
               1741,
               1754,
               1864,
               1890],
              'cube18_cluster0': [8,
               20,
               242,
               276,
               408,
               562,
               61

In [20]:
mapper.visualize(graph,path_html = "mapper_visualization_output_umap2.html")

Wrote visualization to: mapper_visualization_output_umap2.html


'<!DOCTYPE html>\n<html>\n\n<head>\n  <meta charset="utf-8">\n  <meta name="generator" content="KeplerMapper">\n  <title>Kepler Mapper | KeplerMapper</title>\n\n  <link rel="icon" type="image/png" href="http://i.imgur.com/axOG6GJ.jpg" />\n\n  <link href=\'https://fonts.googleapis.com/css?family=Roboto+Mono:700,300\' rel=\'stylesheet\' type=\'text/css\'>\n  <style>* {\n  margin: 0;\n  padding: 0;\n}\n\nhtml, body {\n  height: 100%;\n}\n\nbody {\n  font-family: "Roboto Mono", "Helvetica", sans-serif;\n  font-size: 14px;\n}\n\n#logo {\n  width:  85px;\n  height: 85px;\n}\n\n#display {\n  color: #95A5A6;\n  background: #212121;\n}\n\n#header {\n  background: #111111;\n}\n\n#print {\n  color: #000;\n  background: #FFF;\n}\n\nh1 {\n  font-size: 21px;\n  font-weight: 300;\n  font-weight: 300;\n}\n\nh2 {\n  font-size: 18px;\n  padding-bottom: 20px;\n  font-weight: 300;\n}\n\nh3 {\n  font-size: 14px;\n  font-weight: 700;\n  text-transform: uppercase;\n}\n\nh4 {\n  font-size: 13px;\n  font-weigh

In [21]:
import umap.umap_ as umap
projected_data = mapper.fit_transform(M, projection=umap.UMAP(n_components=3, n_neighbors=15,min_dist=0.3,))
projected_data.shape

..Composing projection pipeline of length 1:
	Projections: UMAP(min_dist=0.3, n_components=3)
	Distance matrices: False
	Scalers: MinMaxScaler()
..Projecting on data shaped (2000, 1600)

..Projecting data using: 
	UMAP(min_dist=0.3, n_components=3, verbose=1)

UMAP(min_dist=0.3, n_components=3, verbose=1)
Tue Jun 27 10:29:14 2023 Construct fuzzy simplicial set
Tue Jun 27 10:29:16 2023 Finding Nearest Neighbors
Tue Jun 27 10:29:16 2023 Finished Nearest Neighbor Search
Tue Jun 27 10:29:16 2023 Construct embedding


Epochs completed:   0%|            0/500 [00:00]

Tue Jun 27 10:29:18 2023 Finished embedding

..Scaling with: MinMaxScaler()



(2000, 3)

In [22]:
cover = km.Cover(n_cubes=10,verbose =0)
graph = mapper.map(projected_data, M, clusterer = sklearn.cluster.DBSCAN(eps=100, min_samples=10), cover = cover)
graph

Mapping on data shaped (2000, 1600) using lens shaped (2000, 3)

Creating 1000 hypercubes.

Created 5126 edges and 569 nodes in 0:00:00.443071.


{'nodes': defaultdict(list,
             {'cube5_cluster0': [247,
               413,
               567,
               658,
               720,
               884,
               1087,
               1157,
               1216,
               1330,
               1390,
               1458,
               1671,
               1815],
              'cube8_cluster0': [125,
               195,
               196,
               360,
               441,
               508,
               824,
               1183,
               1241,
               1486,
               1534,
               1632,
               1724,
               1795,
               1979],
              'cube9_cluster0': [88,
               136,
               195,
               196,
               340,
               360,
               421,
               422,
               441,
               508,
               1063,
               1183,
               1241,
               1486,
               1979],
              '

In [23]:
mapper.visualize(graph,path_html = "mapper_visualization_output_umap3.html")

Wrote visualization to: mapper_visualization_output_umap3.html


'<!DOCTYPE html>\n<html>\n\n<head>\n  <meta charset="utf-8">\n  <meta name="generator" content="KeplerMapper">\n  <title>Kepler Mapper | KeplerMapper</title>\n\n  <link rel="icon" type="image/png" href="http://i.imgur.com/axOG6GJ.jpg" />\n\n  <link href=\'https://fonts.googleapis.com/css?family=Roboto+Mono:700,300\' rel=\'stylesheet\' type=\'text/css\'>\n  <style>* {\n  margin: 0;\n  padding: 0;\n}\n\nhtml, body {\n  height: 100%;\n}\n\nbody {\n  font-family: "Roboto Mono", "Helvetica", sans-serif;\n  font-size: 14px;\n}\n\n#logo {\n  width:  85px;\n  height: 85px;\n}\n\n#display {\n  color: #95A5A6;\n  background: #212121;\n}\n\n#header {\n  background: #111111;\n}\n\n#print {\n  color: #000;\n  background: #FFF;\n}\n\nh1 {\n  font-size: 21px;\n  font-weight: 300;\n  font-weight: 300;\n}\n\nh2 {\n  font-size: 18px;\n  padding-bottom: 20px;\n  font-weight: 300;\n}\n\nh3 {\n  font-size: 14px;\n  font-weight: 700;\n  text-transform: uppercase;\n}\n\nh4 {\n  font-size: 13px;\n  font-weigh

In [24]:
projected_data = mapper.fit_transform(M, projection=umap.UMAP(n_components=3, n_neighbors=10,min_dist=0.3,))
projected_data.shape

..Composing projection pipeline of length 1:
	Projections: UMAP(min_dist=0.3, n_components=3, n_neighbors=10)
	Distance matrices: False
	Scalers: MinMaxScaler()
..Projecting on data shaped (2000, 1600)

..Projecting data using: 
	UMAP(min_dist=0.3, n_components=3, n_neighbors=10, verbose=1)

UMAP(min_dist=0.3, n_components=3, n_neighbors=10, verbose=1)
Tue Jun 27 10:30:58 2023 Construct fuzzy simplicial set
Tue Jun 27 10:31:00 2023 Finding Nearest Neighbors
Tue Jun 27 10:31:00 2023 Finished Nearest Neighbor Search
Tue Jun 27 10:31:00 2023 Construct embedding


Epochs completed:   0%|            0/500 [00:00]

Tue Jun 27 10:31:02 2023 Finished embedding

..Scaling with: MinMaxScaler()



(2000, 3)

In [25]:
cover = km.Cover(n_cubes=10,verbose =0)
graph = mapper.map(projected_data, M, clusterer = sklearn.cluster.DBSCAN(eps=75, min_samples=10), cover = cover)
graph

Mapping on data shaped (2000, 1600) using lens shaped (2000, 3)

Creating 1000 hypercubes.

Created 5074 edges and 582 nodes in 0:00:00.465316.


{'nodes': defaultdict(list,
             {'cube7_cluster0': [9,
               86,
               583,
               1016,
               1028,
               1075,
               1161,
               1164,
               1227,
               1445,
               1485,
               1528,
               1865],
              'cube8_cluster0': [9,
               298,
               583,
               794,
               885,
               887,
               1016,
               1018,
               1028,
               1066,
               1075,
               1161,
               1164,
               1227,
               1445,
               1485,
               1528,
               1662,
               1865],
              'cube9_cluster0': [201,
               298,
               721,
               793,
               794,
               870,
               885,
               887,
               1018,
               1066,
               1146,
               1662,
              

In [26]:
mapper.visualize(graph,path_html = "mapper_visualization_output_umap4.html")

Wrote visualization to: mapper_visualization_output_umap4.html


'<!DOCTYPE html>\n<html>\n\n<head>\n  <meta charset="utf-8">\n  <meta name="generator" content="KeplerMapper">\n  <title>Kepler Mapper | KeplerMapper</title>\n\n  <link rel="icon" type="image/png" href="http://i.imgur.com/axOG6GJ.jpg" />\n\n  <link href=\'https://fonts.googleapis.com/css?family=Roboto+Mono:700,300\' rel=\'stylesheet\' type=\'text/css\'>\n  <style>* {\n  margin: 0;\n  padding: 0;\n}\n\nhtml, body {\n  height: 100%;\n}\n\nbody {\n  font-family: "Roboto Mono", "Helvetica", sans-serif;\n  font-size: 14px;\n}\n\n#logo {\n  width:  85px;\n  height: 85px;\n}\n\n#display {\n  color: #95A5A6;\n  background: #212121;\n}\n\n#header {\n  background: #111111;\n}\n\n#print {\n  color: #000;\n  background: #FFF;\n}\n\nh1 {\n  font-size: 21px;\n  font-weight: 300;\n  font-weight: 300;\n}\n\nh2 {\n  font-size: 18px;\n  padding-bottom: 20px;\n  font-weight: 300;\n}\n\nh3 {\n  font-size: 14px;\n  font-weight: 700;\n  text-transform: uppercase;\n}\n\nh4 {\n  font-size: 13px;\n  font-weigh

In [29]:
cover = km.Cover(n_cubes=10,verbose =0)
graph = mapper.map(projected_data, M, clusterer = sklearn.cluster.DBSCAN(eps=75, min_samples=20), cover = cover)
graph

Mapping on data shaped (2000, 1600) using lens shaped (2000, 3)

Creating 1000 hypercubes.

Created 2711 edges and 374 nodes in 0:00:00.330453.


{'nodes': defaultdict(list,
             {'cube17_cluster0': [9,
               298,
               583,
               794,
               815,
               885,
               887,
               1016,
               1018,
               1066,
               1075,
               1161,
               1164,
               1227,
               1308,
               1445,
               1485,
               1550,
               1608,
               1865,
               1888],
              'cube20_cluster0': [16,
               136,
               149,
               170,
               297,
               340,
               386,
               390,
               421,
               531,
               635,
               636,
               645,
               713,
               844,
               866,
               871,
               1052,
               1152,
               1191,
               1198,
               1296,
               1850,
               1903],
              

In [30]:
mapper.visualize(graph,path_html = "mapper_visualization_output_umap5.html")

Wrote visualization to: mapper_visualization_output_umap5.html


'<!DOCTYPE html>\n<html>\n\n<head>\n  <meta charset="utf-8">\n  <meta name="generator" content="KeplerMapper">\n  <title>Kepler Mapper | KeplerMapper</title>\n\n  <link rel="icon" type="image/png" href="http://i.imgur.com/axOG6GJ.jpg" />\n\n  <link href=\'https://fonts.googleapis.com/css?family=Roboto+Mono:700,300\' rel=\'stylesheet\' type=\'text/css\'>\n  <style>* {\n  margin: 0;\n  padding: 0;\n}\n\nhtml, body {\n  height: 100%;\n}\n\nbody {\n  font-family: "Roboto Mono", "Helvetica", sans-serif;\n  font-size: 14px;\n}\n\n#logo {\n  width:  85px;\n  height: 85px;\n}\n\n#display {\n  color: #95A5A6;\n  background: #212121;\n}\n\n#header {\n  background: #111111;\n}\n\n#print {\n  color: #000;\n  background: #FFF;\n}\n\nh1 {\n  font-size: 21px;\n  font-weight: 300;\n  font-weight: 300;\n}\n\nh2 {\n  font-size: 18px;\n  padding-bottom: 20px;\n  font-weight: 300;\n}\n\nh3 {\n  font-size: 14px;\n  font-weight: 700;\n  text-transform: uppercase;\n}\n\nh4 {\n  font-size: 13px;\n  font-weigh

In [33]:
cover = km.Cover(n_cubes=8,verbose =0)
graph = mapper.map(projected_data, M, clusterer = sklearn.cluster.DBSCAN(eps=75, min_samples=30), cover = cover)
graph

Mapping on data shaped (2000, 1600) using lens shaped (2000, 3)

Creating 512 hypercubes.

Created 1806 edges and 235 nodes in 0:00:00.289080.


{'nodes': defaultdict(list,
             {'cube13_cluster0': [9,
               44,
               86,
               201,
               220,
               298,
               583,
               695,
               794,
               815,
               885,
               887,
               1016,
               1018,
               1028,
               1038,
               1066,
               1075,
               1146,
               1161,
               1164,
               1227,
               1308,
               1445,
               1485,
               1495,
               1528,
               1550,
               1608,
               1788,
               1865,
               1888],
              'cube16_cluster0': [16,
               57,
               105,
               170,
               340,
               390,
               422,
               528,
               531,
               601,
               635,
               645,
               713,
               753,

In [34]:
mapper.visualize(graph,path_html = "mapper_visualization_output_umap6.html")

Wrote visualization to: mapper_visualization_output_umap6.html


'<!DOCTYPE html>\n<html>\n\n<head>\n  <meta charset="utf-8">\n  <meta name="generator" content="KeplerMapper">\n  <title>Kepler Mapper | KeplerMapper</title>\n\n  <link rel="icon" type="image/png" href="http://i.imgur.com/axOG6GJ.jpg" />\n\n  <link href=\'https://fonts.googleapis.com/css?family=Roboto+Mono:700,300\' rel=\'stylesheet\' type=\'text/css\'>\n  <style>* {\n  margin: 0;\n  padding: 0;\n}\n\nhtml, body {\n  height: 100%;\n}\n\nbody {\n  font-family: "Roboto Mono", "Helvetica", sans-serif;\n  font-size: 14px;\n}\n\n#logo {\n  width:  85px;\n  height: 85px;\n}\n\n#display {\n  color: #95A5A6;\n  background: #212121;\n}\n\n#header {\n  background: #111111;\n}\n\n#print {\n  color: #000;\n  background: #FFF;\n}\n\nh1 {\n  font-size: 21px;\n  font-weight: 300;\n  font-weight: 300;\n}\n\nh2 {\n  font-size: 18px;\n  padding-bottom: 20px;\n  font-weight: 300;\n}\n\nh3 {\n  font-size: 14px;\n  font-weight: 700;\n  text-transform: uppercase;\n}\n\nh4 {\n  font-size: 13px;\n  font-weigh